In [1]:
import pandas as pd
import os
import numpy as np
from sklearn.model_selection import train_test_split
from keras.models import Sequential
from keras.layers import Dense
from keras.optimizers import Adam
from matplotlib import pyplot as plt

# Data Preprocessing

In [2]:
directory = './temperature-breach-data'
subf = ['transport','waiting']
direc = []
for filename in os.listdir(directory):
    fn = os.path.join(directory, filename)
    direc.append(fn)
print(direc)

['./temperature-breach-data\\breakdown of vehicle during road ransport', './temperature-breach-data\\congestion at port', './temperature-breach-data\\door open', './temperature-breach-data\\incorrect container settings', './temperature-breach-data\\normal', './temperature-breach-data\\reefer cooling unit malfunction', './temperature-breach-data\\shipment delay due to poor doc', './temperature-breach-data\\without precool']


In [3]:
def preprocess(fn):
    
    with open(fn) as f:
        data = (f.readlines())[1:]
    for j in range(len(data)):                                     # Data Preprocessing (Splitting of string i.e. input from notepad)
        if "," in data[j]:
            data[j]=data[j].split(",")
        else:
            data[j]=data[j].split(" ")
        data[j] = list(filter(lambda a: a != "", data[j]))
        data[j] = list(filter(lambda a: a != "\n", data[j]))       # Filter spaces and '\n' from the split data
        data[j] = data[j][1:]
        for k in range(len(data[j])):
            #print(data[j][k])
            try:
                data[j][k] = float(data[j][k])
            except:
                data[j][k] = float(data[j][k].strip(" \n"))        # Convert data values to float

    sensor_temp=[data[-13][-1],data[7][-1]]

    for j in range(len(data)):
        data[j] = sensor_temp+data[j]  
    
    return data

In [4]:
f_data = []
for i in direc:
    for filename in os.listdir(i):
        fn = os.path.join(i, filename)
        if os.path.isfile(fn):
            data = preprocess(fn)[:]
            f_data+=data  
            
    for j in subf:
        j_pa = os.path.join(i,j)
        try:
            tmp = os.listdir(j_pa)
        except:
            continue
        for filename in tmp:
            fn = os.path.join(j_pa, filename)
            data = preprocess(fn)[:]
            f_data+=data              

In [5]:
len(f_data)

864050

In [6]:
print(f_data[-5:])

[[283.7153015, 284.1513367, 0.150000006, -2.500000238, 0.6000000834, 283.2873535], [283.7153015, 284.1513367, -0.6200000048, -2.880000114, 1.870000005, 285.3923035], [283.7153015, 284.1513367, -1.100000024, -4.170000076, 1.789999962, 283.6853638], [283.7153015, 284.1513367, -1.299999952, -2.549999952, 1.580000043, 283.8962097], [283.7153015, 284.1513367, 0.1299999952, -3.799999952, 1.299999952, 283.3642883]]


In [7]:
df = pd.DataFrame(f_data, columns =['Sensor 1 Temp', 'Sensor 2 Temp','X','Y','Z','Temp'])
df.head()

Sensor 1 Temp  Sensor 2 Temp     X     Y      Z        Temp
0     287.065491     288.838776 -0.62 -3.90  1.480  307.927795
1     287.065491     288.838776 -0.43 -3.02  0.109  307.975678
2     287.065491     288.838776 -0.62 -3.20  0.880  307.851410
3     287.065491     288.838776 -0.02 -3.58  0.480  307.797028
4     287.065491     288.838776 -0.64 -4.05  0.520  300.472473

In [8]:
df.to_csv('data_15-01.csv')

In [9]:
df.shape

(864050, 6)

In [10]:
data = f_data

In [11]:
X = np.array([i[:-1] for i in data])
Y = np.array([[i[-1]] for i in data])

In [12]:
X_train_in, X_test_in, Y_train, Y_test = train_test_split(X, Y, test_size=0.2, random_state=42)

In [13]:
X_train_in.shape

(691240, 5)

In [14]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler
scaler=MinMaxScaler()
scaler.fit(X_train_in)

X_train = scaler.transform(X_train_in)
X_test = scaler.transform(X_test_in)

In [15]:
import pickle
scalerfile = 'standscaler.sav'                             # Saving of Min Max Scaler
pickle.dump(scaler, open(scalerfile, 'wb'))

# Model

In [15]:
from sklearn.ensemble import RandomForestRegressor

#model = RandomForestRegressor(n_estimators = 500,max_depth=7, random_state=0)
model = RandomForestRegressor()
model.fit(X_train,Y_train)

C:\Users\Punyatoya\AppData\Local\Temp\ipykernel_8940\68697856.py:5: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  model.fit(X_train,Y_train)


RandomForestRegressor()

In [54]:
from xgboost import XGBRegressor

#model = XGBRegressor(num_parallel_tree=3,max_depth=3,eta=0.1)
model = XGBRegressor()
model.fit(X_train,Y_train)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=None, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=None, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             n_estimators=100, n_jobs=None, num_parallel_tree=None,
             predictor=None, random_state=None, ...)

In [16]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
print(mean_absolute_error(model.predict(X_test), Y_test))
print(mean_squared_error(model.predict(X_test), Y_test))
print(mean_absolute_error(model.predict(X_train), Y_train))
print(mean_squared_error(model.predict(X_train), Y_train))

0.08557189661288254
0.19450161211723432
0.031809737365863594
0.02658917826102448


In [36]:
import pickle
filename = 'rf_minmax.sav'
pickle.dump(model, open(filename, 'wb'))

In [17]:
rel_model = model

# Validation-1

In [57]:
filename = 'xgb_minmax.sav'
rel_model = pickle.load(open(filename, 'rb'))

In [58]:
scalerfile = 'scaler.sav'
#scalerfile = 'standscaler.sav'
scaler = pickle.load(open(scalerfile, 'rb'))

In [18]:
dataframe1 = pd.read_excel('expt-data for validation.xlsx')
dataframe1.head()

Unnamed: 0 Unnamed: 1 Experimental Data Unnamed: 3 Unnamed: 4 Unnamed: 5  \
0     Node-1     Node-2            Node-3     Node-4     Node-5     Node-6   
1       26.8      29.52               NaN       28.3       23.8       24.3   
2       26.8      29.52               NaN       28.2       23.8       24.3   
3       26.8      29.52               NaN       28.2       23.8       24.3   
4       26.8      29.52               NaN       28.2       23.8       24.3   

  Unnamed: 6  
0     Node-7  
1        NaN  
2        NaN  
3        NaN  
4        NaN

In [19]:
X = dataframe1.iloc[1:,[5,0]]
X = X+273
X.columns = ['Sensor 1','Sensor 2']

In [20]:
val_Y = dataframe1.iloc[1:,[1,2,3,4,6]]
val_Y.columns = ['Node2','Node 3','Node 4','Node 5','Node 7']
val_Y = val_Y + 273

In [21]:
coord = [
    [-0.64,-4.05,0.52],
    [-0.3,-4.03,0.01],
    [-0.82,-1.7,0.8],
    [-0.62,-2.88,1.87],
    [-0.3,-1.55,1.72]
]
fin_res = pd.DataFrame()

In [22]:
count=0
for i in coord:
    X['X'] = [i[0]]*(X.shape[0])
    X['Y'] = [i[1]]*(X.shape[0])
    X['Z'] = [i[2]]*(X.shape[0])
    print(X.head(20))
    val_X = X.to_numpy()
    #scaler.fit(val_X)
    out_val = rel_model.predict(scaler.transform(val_X))
    fin_res[val_Y.columns[count]] = pd.Series (out_val.flatten())
    count+=1

   Sensor 1 Sensor 2     X     Y     Z
1     297.3    299.8 -0.64 -4.05  0.52
2     297.3    299.8 -0.64 -4.05  0.52
3     297.3    299.8 -0.64 -4.05  0.52
4     297.3    299.8 -0.64 -4.05  0.52
5     297.3    299.8 -0.64 -4.05  0.52
6     297.3    299.8 -0.64 -4.05  0.52
7     297.4    299.6 -0.64 -4.05  0.52
8     297.4    299.5 -0.64 -4.05  0.52
9     297.4    299.4 -0.64 -4.05  0.52
10    297.4    299.3 -0.64 -4.05  0.52
11    297.4    299.2 -0.64 -4.05  0.52
12    297.4      299 -0.64 -4.05  0.52
13    297.5    298.8 -0.64 -4.05  0.52
14    297.5    298.7 -0.64 -4.05  0.52
15    297.5    298.5 -0.64 -4.05  0.52
16    297.5    298.4 -0.64 -4.05  0.52
17    297.6    298.2 -0.64 -4.05  0.52
18    297.6    298.1 -0.64 -4.05  0.52
19    297.6    297.9 -0.64 -4.05  0.52
20    297.6    297.7 -0.64 -4.05  0.52
   Sensor 1 Sensor 2    X     Y     Z
1     297.3    299.8 -0.3 -4.03  0.01
2     297.3    299.8 -0.3 -4.03  0.01
3     297.3    299.8 -0.3 -4.03  0.01
4     297.3    299.8 -0.3 -4.

In [23]:
test = fin_res - val_Y
test['Sensor 1']  = X['Sensor 1']
test['Sensor 2']  = X['Sensor 2']
test = test.astype(float)
test = test.abs()
pd.set_option('display.max_rows', None)

In [24]:
test.describe()

Node2      Node 3      Node 4      Node 5     Node 7    Sensor 1  \
count  936.000000  889.000000  235.000000  936.000000  93.000000  937.000000   
mean     3.536256    4.275178   10.203725   10.035881  18.300590  290.351761   
std      2.082836    2.994986    7.865688    6.729579   0.557793    3.608484   
min      0.005548    0.007613    0.049638    0.012160  17.647030  283.100000   
25%      1.950921    2.454445    3.631411    2.995662  17.755316  290.300000   
50%      3.777795    3.662364    8.032222    9.504125  18.143083  291.400000   
75%      4.554316    5.558667   14.993960   16.194797  18.819571  291.700000   
max     10.509103   12.345555   23.618301   19.861920  18.929209  298.000000   

         Sensor 2  
count  937.000000  
mean   289.456350  
std      4.603193  
min    283.700000  
25%    284.600000  
50%    290.100000  
75%    291.700000  
max    299.800000

# Validation - 2

In [2]:
import pickle
filename = 'rf_minmax.sav'
rel_model = pickle.load(open(filename, 'rb'))

In [3]:
scalerfile = 'scaler.sav'
#scalerfile = 'standscaler.sav'
scaler = pickle.load(open(scalerfile, 'rb'))

In [135]:
# from sklearn.metrics import mean_squared_error
# a = rel_model.predict(scaler.transform(X))-Y
# ch = pd.DataFrame()
# ch['test'] = pd.Series(a.flatten())
# ch = ch.abs()
# ch.describe()

27002/27002 [==============================] - 58s 2ms/step


In [4]:
dataframe1 = pd.read_excel('expt-data for validationfinal.xlsx')

In [5]:
dataframe1

Unnamed: 0  node-1 (sensor-2)    nodel-2     node-3     node-4  \
0             NaN          34.800000  30.350000  35.740000  33.573333   
1             NaN          34.800000  30.350000  35.640000  33.573333   
2             NaN          34.800000  30.340000  35.440000  33.573333   
3             NaN          34.800000  30.340000  35.240000  33.573333   
4             NaN          34.800000  30.320000  35.100000  33.573333   
...           ...                ...        ...        ...        ...   
16092         NaN          11.041313  10.909961   9.971705   9.969400   
16093         NaN          11.036602  10.906125   9.966910   9.969400   
16094         NaN          11.031892  10.902290   9.962115   9.969400   
16095         NaN          11.027181  10.898454   9.957321   9.969400   
16096         NaN          11.022471  10.894618   9.952526   9.969400   

          node-5  node-6 (sensor-1)     node-7  
0      24.600000           25.00000  26.000000  
1      24.600000           25.00000  25.900000  
2      24.600000           25.00000  25.800000  
3      24.500000           25.00000  25.700000  
4      24.500000           25.00000  25.700000  
...          ...                ...        ...  
16092  10.008635            9.95014   9.953093  
16093  10.008635            9.95014   9.953093  
16094  10.008635            9.95014   9.953093  
16095  10.008635            9.95014   9.953093  
16096  10.008635            9.95014   9.953093  

[16097 rows x 8 columns]

In [6]:
X = dataframe1.iloc[:,[6,1]]
X = X+273
X.columns = ['Sensor 1','Sensor 2']

In [7]:
X

Sensor 1    Sensor 2
0      298.00000  307.800000
1      298.00000  307.800000
2      298.00000  307.800000
3      298.00000  307.800000
4      298.00000  307.800000
...          ...         ...
16092  282.95014  284.041313
16093  282.95014  284.036602
16094  282.95014  284.031892
16095  282.95014  284.027181
16096  282.95014  284.022471

[16097 rows x 2 columns]

In [8]:
val_Y = dataframe1.iloc[:,[2,3,4,5,7]]
val_Y.columns = ['Node 2','Node 3','Node 4','Node 5','Node 7']
val_Y = val_Y + 273

In [9]:
val_Y

Node 2      Node 3      Node 4      Node 5      Node 7
0      303.350000  308.740000  306.573333  297.600000  299.000000
1      303.350000  308.640000  306.573333  297.600000  298.900000
2      303.340000  308.440000  306.573333  297.600000  298.800000
3      303.340000  308.240000  306.573333  297.500000  298.700000
4      303.320000  308.100000  306.573333  297.500000  298.700000
...           ...         ...         ...         ...         ...
16092  283.909961  282.971705  282.969400  283.008635  282.953093
16093  283.906125  282.966910  282.969400  283.008635  282.953093
16094  283.902290  282.962115  282.969400  283.008635  282.953093
16095  283.898454  282.957321  282.969400  283.008635  282.953093
16096  283.894618  282.952526  282.969400  283.008635  282.953093

[16097 rows x 5 columns]

In [10]:
coord = [
    [-0.64,-4.05,0.52],
    [-0.3,-4.03,0.01],
    [-0.82,-1.7,0.8],
    [-0.62,-2.88,1.87],
    [-0.3,-1.55,1.72]
]
fin_res = pd.DataFrame()

In [11]:
count=0
for i in coord:
    X['X'] = [i[0]]*(X.shape[0])
    X['Y'] = [i[1]]*(X.shape[0])
    X['Z'] = [i[2]]*(X.shape[0])
    print(X.head(20))
    val_X = X.to_numpy()
    #scaler.fit(val_X)
    out_val = rel_model.predict(scaler.transform(val_X))
    fin_res[val_Y.columns[count]] = pd.Series (out_val.flatten())
    count+=1

    Sensor 1  Sensor 2     X     Y     Z
0      298.0     307.8 -0.64 -4.05  0.52
1      298.0     307.8 -0.64 -4.05  0.52
2      298.0     307.8 -0.64 -4.05  0.52
3      298.0     307.8 -0.64 -4.05  0.52
4      298.0     307.8 -0.64 -4.05  0.52
5      298.0     307.8 -0.64 -4.05  0.52
6      297.9     307.8 -0.64 -4.05  0.52
7      297.9     307.8 -0.64 -4.05  0.52
8      297.9     307.8 -0.64 -4.05  0.52
9      297.9     307.8 -0.64 -4.05  0.52
10     297.9     307.8 -0.64 -4.05  0.52
11     297.9     307.8 -0.64 -4.05  0.52
12     297.9     307.8 -0.64 -4.05  0.52
13     297.8     307.8 -0.64 -4.05  0.52
14     297.8     307.8 -0.64 -4.05  0.52
15     297.8     307.8 -0.64 -4.05  0.52
16     297.8     307.8 -0.64 -4.05  0.52
17     297.7     307.8 -0.64 -4.05  0.52
18     297.7     307.8 -0.64 -4.05  0.52
19     297.7     307.8 -0.64 -4.05  0.52
    Sensor 1  Sensor 2    X     Y     Z
0      298.0     307.8 -0.3 -4.03  0.01
1      298.0     307.8 -0.3 -4.03  0.01
2      298.0     30

In [12]:
test = fin_res - val_Y
test['Sensor 1']  = X['Sensor 1']
test['Sensor 2']  = X['Sensor 2']
test = test.astype(float)
test = test.abs()
pd.set_option('display.max_rows', None)

In [13]:
test

Node 2     Node 3     Node 4     Node 5     Node 7    Sensor 1  \
0       4.498815   7.571544   6.627633   1.958676   0.036519  298.000000   
1       4.498815   7.471544   6.627633   1.958676   0.136519  298.000000   
2       4.488815   7.271544   6.627633   1.958676   0.236519  298.000000   
3       4.488815   7.071544   6.627633   1.858676   0.336519  298.000000   
4       4.468815   6.931544   6.627633   1.858676   0.336519  298.000000   
5       4.468815   6.931544   6.627633   1.858676   0.336519  298.000000   
6       4.458815   6.911544   6.627633   1.858676   0.336519  297.900000   
7       4.448815   6.911544   6.494300   1.858676   0.336519  297.900000   
8       4.428815   6.871544   6.494300   1.758676   0.336519  297.900000   
9       4.428815   6.871544   6.494300   1.758676   0.436519  297.900000   
10      3.668815   6.851544   6.494300   1.658676   0.436519  297.900000   
11      3.668815   6.831544   6.494300   1.658676   0.436519  297.900000   
12      3.668815   6.791544   6.494300   1.658676   0.436519  297.900000   
13      3.668815   6.791544   6.494300   1.658676   0.436519  297.800000   
14      3.668815   6.671544   6.494300   1.658676   0.436519  297.800000   
15      3.668815   6.471544   6.494300   1.558676   0.436519  297.800000   
16      3.668815   6.271544   6.494300   1.558676   0.436519  297.800000   
17      3.668815   6.171544   6.427633   1.558676   0.436519  297.700000   
18      3.668815   5.971544   6.360967   1.558676   0.536519  297.700000   
19      3.668815   5.771544   6.360967   1.558676   0.536519  297.700000   
20      3.668815   5.671544   6.294300   1.558676   0.536519  297.700000   
21      3.668815   5.571544   6.227633   1.458676   0.536519  297.700000   
22      3.668815   5.471544   6.160967   1.458676   0.536519  297.700000   
23      3.668815   5.371544   6.160967   1.458676   0.636519  297.700000   
24      3.668815   5.251544   6.160967   1.458676   0.636519  297.700000   
25      3.668815   5.191544   6.027633   1.458676   0.636519  297.600000   
26      3.668815   5.171544   6.027633   1.358676   0.636519  297.600000   
27      3.668815   5.171544   6.027633   1.358676   0.636519  297.600000   
28      3.668815   5.151544   6.027633   1.358676   0.736519  297.600000   
29      3.668815   5.091544   6.027633   1.358676   0.736519  297.600000   
30      3.668815   5.071544   5.894300   1.358676   0.736519  297.600000   
31      3.668815   5.011544   5.894300   1.358676   0.736519  297.600000   
32      3.668815   4.891544   5.894300   1.258676   0.736519  297.600000   
33      3.668815   4.871544   5.894300   1.258676   0.736519  297.500000   
34      3.668815   4.811544   5.760967   1.258676   0.836519  297.500000   
35      3.668815   4.804877   5.760967   1.258676   0.836519  297.500000   
36      3.668815   4.804877   5.760967   1.258676   0.836519  297.500000   
37      3.668815   4.804877   5.694300   1.258676   0.936519  297.500000   
38      3.668815   4.804877   5.694300   1.158676   0.936519  297.500000   
39      3.668815   4.804877   5.627633   1.158676   0.936519  297.400000   
40      3.668815   4.804877   5.627633   1.158676   0.936519  297.400000   
41      3.668815   4.804877   5.627633   1.158676   0.936519  297.400000   
42      3.668815   4.791544   5.627633   1.158676   0.936519  297.400000   
43      3.668815   4.771544   5.627633   1.158676   1.036519  297.400000   
44      3.668815   4.751544   5.560967   1.158676   1.036519  297.400000   
45      3.668815   4.671544   5.494300   1.058676   1.036519  297.400000   
46      2.228815   4.671544   5.427633   1.058676   1.036519  297.400000   
47      2.228815   4.671544   5.427633   1.058676   1.036519  297.400000   
48      2.228815   4.671544   5.427633   1.058676   1.036519  297.300000   
49      2.228815   4.651544   5.360967   0.958676   1.036519  297.300000   
50      2.228815   4.621544   5.294300   0.958676   1.036519  297.300000   
51      2.228815   4.621544   5.294300   0.958676   1.1365

In [14]:
test.describe()

Node 2        Node 3        Node 4        Node 5        Node 7  \
count  16097.000000  16097.000000  16097.000000  16097.000000  16097.000000   
mean       1.822568      1.188360      6.528582      5.105547      5.301218   
std        3.345563      2.573659      3.342943      3.372890      2.745045   
min        0.006821      0.000761      0.000236      0.041324      0.036519   
25%        0.305597      0.307545      5.576484      3.946403      4.596222   
50%        0.815795      0.644093      6.541380      4.267173      4.966463   
75%        1.272381      0.795202      6.862858      4.862446      5.107065   
max       16.919436     14.033275     20.503446     21.006286     17.573214   

           Sensor 1      Sensor 2  
count  16097.000000  16097.000000  
mean     286.816798    287.680952  
std        1.430950      2.830792  
min      282.950140    284.022471  
25%      286.700000    286.320000  
50%      286.800000    287.246667  
75%      286.900000    287.383333  
max      298.000000    307.800000